In [1]:
import pandas as pd
#import numpy as np
#import glob
#import os
from datetime import datetime as dt
from datetime import timedelta as td
import plotly.graph_objects as go
import plotly.express as px
import ipywidgets as widgets
import plotly.figure_factory as figfact

In [2]:
df=pd.read_json('diff_df_small.json')

In [8]:
fig2=figfact.create_2d_density(
    df.hpc_x_arcsec/df.rsun_obs, df.hpc_y_arcsec/df.rsun_obs, colorscale='Blues', point_size=5,ncontours=10,title='STIX Flare Locations')
fig2.add_shape(type="circle",
    xref="x", yref="y",
    x0=-1, y0=-1, x1=1, y1=1,
    line_color="LightSeaGreen",
)
fig2.update_layout(xaxis_title='x (fraction Rsun)',xaxis_range=[-1.5,1.5],yaxis_range=[-1.5,1.5])
fig2.update_layout(yaxis_title='y (fraction Rsun)')

def response_method(change):
    temp_df = df[df.method==method.value]
    try:
        elow=int(erange.value[:erange.value.find('-')])
        temp_df = temp_df[temp_df.Energy_low==elow]
    except ValueError:
        pass
    ftemp=figfact.create_2d_density(
    temp_df.hpc_x_arcsec/temp_df.rsun_obs, temp_df.hpc_y_arcsec/temp_df.rsun_obs, colorscale='Blues', point_size=5,ncontours=10)

    with g2.batch_update():
        for i,d in enumerate(g2.data):
            g2.data[i]['x'] = ftemp.data[i]['x']
            g2.data[i]['y'] = ftemp.data[i]['y']
        g2.layout.title = f"{method.value} Flare Locations {erange.value}, {temp_df['_id_x'].nunique()} flares"

options=df.method.unique()
method=widgets.Dropdown(options=options,value=options[0],description='Algorithm',disabled=False)
erange=widgets.Dropdown(options=['All','4-10 keV','16-28 keV'],value='All',description='Energy',disabled=False)
#g1=go.FigureWidget(data=fig.data,layout=fig.layout)
g2=go.FigureWidget(data=fig2.data,layout=fig2.layout)
method.observe(response_method,names="value")
erange.observe(response_method,names="value")
container = widgets.HBox([method, erange])
widgets.VBox([container,g2])

**note:** if you have run the cell at the end (with the second widget), this one will no longer work! re-run the cell to get back the correct behavior

In [9]:
fig3=figfact.create_2d_density(
    df.rotated_x_arcsec/df.rsun_obs, df.rotated_y_arcsec/df.rsun_obs, colorscale='Blues', point_size=5,ncontours=10,title='AIA Flare Locations (STIX perspective)')
fig3.add_shape(type="circle",
    xref="x", yref="y",
    x0=-1, y0=-1, x1=1, y1=1,
    line_color="LightSeaGreen",
)
fig3.update_layout(xaxis_title='HPC x (fraction Rsun)',xaxis_range=[-1.5,1.5],yaxis_range=[-1.5,1.5])
fig3.update_layout(yaxis_title='HPC y (fraction Rsun)')


## Coordinate Differences

In [6]:
fig=figfact.create_2d_density(
    df.diff_x, df.diff_y, colorscale='Blues', point_size=5,ncontours=10,title='Difference with AIA Flare Locations')
fig.add_shape(type="circle",
    xref="x", yref="y",
    x0=-1, y0=-1, x1=1, y1=1,
    line_color="LightSeaGreen",
)
fig.update_layout(xaxis_title='Difference x (arcsec)',xaxis_range=[-500,500],yaxis_range=[-500,500])
fig.update_layout(yaxis_title='Difference y (arcsec)')


In [7]:
def response(change):
    temp_df = df[df.method==method.value]
    try:
        elow=int(erange.value[:erange.value.find('-')])
        temp_df = temp_df[temp_df.Energy_low==elow]
    except ValueError:
        pass
    
    dkeyx='diff_x'
    dkeyy='diff_y'
    gkey='rotated_x_arcsec'
    if comp.value =='BPROJ':
        dkeyx='diff_bp_x'
        dkeyy='diff_bp_y'
        gkey='hpc_x_arcsec'
    ftemp=figfact.create_2d_density(
    temp_df[dkeyx], temp_df[dkeyy], colorscale='Blues', point_size=5,ncontours=10)
    nflares=temp_df.groupby('_id_x')[gkey].first().notna().sum() #number AIA flares
    with g1.batch_update():
        for i,d in enumerate(g2.data):
            g1.data[i]['x'] = ftemp.data[i]['x']
            g1.data[i]['y'] = ftemp.data[i]['y']
        g1.layout.title = f"{method.value} - {comp.value} locations, {nflares} flares"

options=df.method.unique()
method=widgets.Dropdown(options=options,value=options[0],description='Algorithm',disabled=False)
erange=widgets.Dropdown(options=['All','4-10 keV','16-28 keV'],value='All',description='Energy',disabled=False)
comp=widgets.Dropdown(options=['AIA','BPROJ'],value='AIA',description='Compare with',disabled=False)
g1=go.FigureWidget(data=fig.data,layout=fig.layout)
method.observe(response,names="value")
erange.observe(response,names="value")
comp.observe(response,names="value")
container = widgets.HBox([method,erange,comp])
widgets.VBox([container,g1])